看看均线策略。

In [1]:
import pandas as pd
from datetime import datetime
import trdb2py

isStaticImg = False
width = 960
height = 768

pd.options.display.max_columns = None
pd.options.display.max_rows = None

trdb2cfg = trdb2py.loadConfig('./trdb2.yaml')

我们先指定一个特定的基金，特定的时间段来分析吧。

In [2]:
# 具体基金
asset = 'jrj.510310'

# 起始时间，0表示从最开始算起
tsStart = 0
# tsStart = trdb2py.str2timestamp('2019-01-01', '%Y-%m-%d')

# 结束时间，-1表示到现在为止
tsEnd = -1
# tsEnd = trdb2py.str2timestamp('2020-01-01', '%Y-%m-%d')

# 初始资金池
paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

# 买入参数，用全部的钱来买入（也就是复利）
paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

# 卖出参数，全部卖出
paramssell = trdb2py.trading2_pb2.SellParams(
    perVolume=1,
)

首先看看这个基金的基准表现，就是在开始时间就直接买入，然后一直持有，看具体的收益率。

In [3]:
# baseline    
s0 = trdb2py.trading2_pb2.Strategy(
    name="normal",
    asset=trdb2py.str2asset(asset),         
)
        
buy0 = trdb2py.trading2_pb2.CtrlCondition(
    name='buyandhold',
)

paramsbuy = trdb2py.trading2_pb2.BuyParams(
    perHandMoney=1,
)

paramsinit = trdb2py.trading2_pb2.InitParams(
    money=10000,
)

s0.buy.extend([buy0])
s0.paramsBuy.CopyFrom(paramsbuy)
s0.paramsInit.CopyFrom(paramsinit)        
p0 = trdb2py.trading2_pb2.SimTradingParams(
    assets=[trdb2py.str2asset(asset)],
    startTs=tsStart,
    endTs=tsEnd,
    strategies=[s0],
    title='baseline',
)  

pnlBaseline = trdb2py.simTrading(trdb2cfg, p0)
trdb2py.showPNL(pnlBaseline, toImg=isStaticImg, width=width, height=height)

那么策略基准线大概就是这样了，7年多的时间2.2倍。

接下来，测一下均线

In [4]:
lstparams = []

for ema in range(2, 61):    
    buy0 = trdb2py.trading2_pb2.CtrlCondition(
        name='indicatorsp',
        operators=['upcross'],
        strVals=['ema.{}'.format(ema)],
    )
    
    buy1 = trdb2py.trading2_pb2.CtrlCondition(
        name='waittostart',
        vals=[ema],
    )    
            
    sell0 = trdb2py.trading2_pb2.CtrlCondition(
        name='indicatorsp',
        operators=['downcross'],
        strVals=['ema.{}'.format(ema)],
    )
    
    s0 = trdb2py.trading2_pb2.Strategy(
        name="normal",
        asset=trdb2py.str2asset(asset),
    )

    s0.buy.extend([buy0, buy1])
    s0.sell.extend([sell0])
    s0.paramsBuy.CopyFrom(paramsbuy)
    s0.paramsSell.CopyFrom(paramssell) 
    s0.paramsInit.CopyFrom(paramsinit)        
    lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
        assets=[trdb2py.str2asset(asset)],
        startTs=tsStart,
        endTs=tsEnd,
        strategies=[s0],
        title='ema{}'.format(ema),
    ))
 
lstpnlmix = trdb2py.simTradings(trdb2cfg, lstparams, ignoreTotalReturn=2.3)

trdb2py.showPNLs(lstpnlmix + [pnlBaseline], toImg=isStaticImg, width=width, height=height)

In [5]:
dfpnl = trdb2py.buildPNLReport(lstpnlmix + [pnlBaseline])

dfpnl1 = dfpnl[dfpnl['totalReturns'] >= 2]

dfpnl1[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)

title  maxDrawdown maxDrawdownStart maxDrawdownEnd  totalReturns  \
4      ema30     0.237838       2017-11-22     2019-01-17      2.743728   
0       ema2     0.261122       2015-05-26     2016-03-01      2.609839   
5      ema31     0.257248       2017-11-22     2019-01-17      2.502286   
3      ema29     0.253262       2017-11-22     2019-01-17      2.495321   
2      ema28     0.256981       2017-11-22     2019-01-17      2.423674   
1      ema27     0.256636       2017-11-22     2019-01-17      2.412460   
6      ema32     0.255309       2017-11-22     2019-01-17      2.405129   
7      ema33     0.245248       2017-11-22     2019-01-17      2.386815   
11     ema55     0.319204       2015-06-08     2016-06-27      2.370634   
9      ema53     0.319204       2015-06-08     2016-06-27      2.358875   
8      ema34     0.238706       2015-06-08     2016-06-27      2.348934   
10     ema54     0.319204       2015-06-08     2016-06-27      2.321168   
12     ema56     0.344055       2015-06-08     2016-06-27      2.303500   
20     ema46     0.339170       2015-06-08     2016-06-27      2.276248   
15     ema51     0.318310       2015-06-08     2016-06-27      2.230978   
21     ema45     0.339170       2015-06-08     2016-06-27      2.212812   
22     ema44     0.330109       2015-06-08     2016-06-27      2.198046   
19     ema47     0.339170       2015-06-08     2016-06-27      2.194556   
13     ema57     0.347322       2015-06-08     2016-06-27      2.188202   
23     ema58     0.347322       2015-06-08     2016-06-27      2.174441   
14     ema52     0.326624       2015-06-08     2016-06-27      2.155742   
17     ema49     0.333232       2015-06-08     2016-06-27      2.149293   
18     ema48     0.333232       2015-06-08     2016-06-27      2.138252   
16     ema50     0.329472       2015-06-08     2016-06-27      2.132860   
26  baseline     0.460140       2015-06-08     2016-01-28      2.077782   
24     ema59     0.382571       2015-06-08     2016-06-27      2.059889   

      sharpe  annualizedReturns  annualizedVolatility  variance  
4   1.372060           0.230482              0.146118  0.334814  
0   1.172821           0.212785              0.155851  0.129945  
5   1.132652           0.198569              0.148827  0.244944  
3   1.131325           0.197648              0.148187  0.243027  
2   1.069201           0.188178              0.147940  0.228500  
1   1.058562           0.186696              0.148027  0.212977  
6   1.034510           0.185727              0.150532  0.243981  
7   1.018788           0.183306              0.150479  0.236530  
11  0.999426           0.181167              0.151254  0.177591  
9   0.989404           0.179613              0.151215  0.181690  
8   0.985547           0.178299              0.150474  0.222048  
10  0.956017           0.174629              0.151283  0.175415  
12  0.942834           0.172294              0.150921  0.160599  
20  0.914673           0.168691              0.151630  0.164051  
15  0.877382           0.162708              0.151254  0.162409  
21  0.860018           0.160307              0.151516  0.153436  
22  0.847896           0.158355              0.151381  0.161582  
19  0.842386           0.157894              0.151823  0.147234  
13  0.843567           0.157054              0.150615  0.146878  
23  0.831862           0.155235              0.150548  0.144998  
14  0.811490           0.152763              0.151281  0.145036  
17  0.805183           0.151911              0.151408  0.142723  
18  0.795732           0.150452              0.151372  0.139027  
16  0.790297           0.149739              0.151511  0.141336  
26  0.486944           0.142459              0.230948  0.108601  
24  0.719628           0.140094              0.152987  0.117328

可以看到，简单的均线策略，最好的情况也就是将上涨的趋势把握住，跳过下跌大的区间，当然，基本上上涨和下跌都会有损失。

这里粒度非常重要，看估计很难看出来，只能试。

In [6]:
lstparams = []

for ema0 in range(2, 61):
    for ema1 in range(2, 61):
        buy0 = trdb2py.trading2_pb2.CtrlCondition(
            name='indicatorsp',
            operators=['upcross'],
            strVals=['ema.{}'.format(ema0)],
        )

        buy1 = trdb2py.trading2_pb2.CtrlCondition(
            name='waittostart',
            vals=[ema0],
        )
        
        buy2 = trdb2py.trading2_pb2.CtrlCondition(
            name='indicatorsp',
            operators=['up'],
            strVals=['ema.{}'.format(ema1)],
        )
        
        buy3 = trdb2py.trading2_pb2.CtrlCondition(
            name='waittostart',
            vals=[ema1],
        )        

        sell0 = trdb2py.trading2_pb2.CtrlCondition(
            name='indicatorsp',
            operators=['downcross'],
            strVals=['ema.{}'.format(ema0)],
        )

        s0 = trdb2py.trading2_pb2.Strategy(
            name="normal",
            asset=trdb2py.str2asset(asset),
        )

        s0.buy.extend([buy0, buy1, buy2, buy3])
        s0.sell.extend([sell0])
        s0.paramsBuy.CopyFrom(paramsbuy)
        s0.paramsSell.CopyFrom(paramssell) 
        s0.paramsInit.CopyFrom(paramsinit)        
        lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
            assets=[trdb2py.str2asset(asset)],
            startTs=tsStart,
            endTs=tsEnd,
            strategies=[s0],
            title='ema{}&ema{}'.format(ema0, ema1),
        ))
 
lstpnlmix = trdb2py.simTradings(trdb2cfg, lstparams, ignoreTotalReturn=3)

# trdb2py.showPNLs(lstpnlmix + [pnlBaseline], toImg=isStaticImg, width=width, height=height)

In [7]:
dfpnl = trdb2py.buildPNLReport(lstpnlmix + [pnlBaseline])

dfpnl1 = dfpnl[dfpnl['totalReturns'] >= 2]

dfpnl1[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)

title  maxDrawdown maxDrawdownStart maxDrawdownEnd  totalReturns  \
30  ema30&ema51     0.174664       2015-06-08     2016-06-27      3.212999   
31  ema30&ema52     0.174664       2015-06-08     2016-06-27      3.193580   
17  ema29&ema51     0.181768       2015-06-08     2016-06-27      3.163432   
29  ema30&ema50     0.174664       2015-06-08     2016-06-27      3.148045   
18  ema29&ema52     0.181768       2015-06-08     2016-06-27      3.144312   
28  ema30&ema49     0.174664       2015-06-08     2016-06-27      3.110444   
4   ema28&ema51     0.181768       2015-06-08     2016-06-27      3.109143   
16  ema29&ema50     0.181768       2015-06-08     2016-06-27      3.099480   
5   ema28&ema52     0.181768       2015-06-08     2016-06-27      3.090352   
26  ema30&ema47     0.174664       2015-06-08     2016-06-27      3.087468   
25  ema30&ema46     0.174664       2015-06-08     2016-06-27      3.087468   
27  ema30&ema48     0.174664       2015-06-08     2016-06-27      3.087468   
15  ema29&ema49     0.181768       2015-06-08     2016-06-27      3.062459   
19  ema30&ema40     0.174664       2015-06-08     2016-06-27      3.061375   
23  ema30&ema44     0.174664       2015-06-08     2016-06-27      3.054106   
24  ema30&ema45     0.174664       2015-06-08     2016-06-27      3.054106   
6   ema29&ema40     0.181768       2015-06-08     2016-06-27      3.047073   
3   ema28&ema50     0.181768       2015-06-08     2016-06-27      3.046289   
20  ema30&ema41     0.174664       2015-06-08     2016-06-27      3.041821   
21  ema30&ema42     0.174664       2015-06-08     2016-06-27      3.041821   
14  ema29&ema48     0.181768       2015-06-08     2016-06-27      3.039837   
13  ema29&ema47     0.181768       2015-06-08     2016-06-27      3.039837   
11  ema29&ema45     0.181768       2015-06-08     2016-06-27      3.039837   
10  ema29&ema44     0.181768       2015-06-08     2016-06-27      3.039837   
12  ema29&ema46     0.181768       2015-06-08     2016-06-27      3.039837   
0   ema27&ema51     0.181768       2015-06-08     2016-06-27      3.035657   
8   ema29&ema42     0.181768       2015-06-08     2016-06-27      3.027611   
7   ema29&ema41     0.181768       2015-06-08     2016-06-27      3.027611   
22  ema30&ema43     0.174664       2015-06-08     2016-06-27      3.023682   
1   ema27&ema52     0.181768       2015-06-08     2016-06-27      3.017310   
2   ema28&ema49     0.181768       2015-06-08     2016-06-27      3.009903   
9   ema29&ema43     0.181768       2015-06-08     2016-06-27      3.009556   
36  ema60&ema49     0.319536       2015-06-08     2016-06-27      2.157534   
39  ema60&ema46     0.319536       2015-06-08     2016-06-27      2.117542   
40  ema60&ema45     0.319536       2015-06-08     2016-06-27      2.112709   
41  ema60&ema44     0.319536       2015-06-08     2016-06-27      2.112709   
37  ema60&ema48     0.319536       2015-06-08     2016-06-27      2.091092   
38  ema60&ema47     0.319536       2015-06-08     2016-06-27      2.091092   
49     baseline     0.460140       2015-06-08     2016-01-28      2.077782   
44  ema60&ema56     0.382571       2015-06-08     2016-06-27      2.025413   
45  ema60&ema57     0.382571       2015-06-08     2016-06-27      2.005961   
46  ema60&ema58     0.382571       2015-06-08     2016-06-27      2.005961   

      sharpe  annualizedReturns  annualizedVolatility  variance  
30  1.930325           0.292509              0.135992  0.457162  
31  1.911165           0.289942              0.136013  0.448614  
17  1.882738           0.285957              0.135950  0.437021  
29  1.863339           0.283924              0.136273  0.431522  
18  1.863870           0.283430              0.135970  0.428830  
28  1.825421           0.278954              0.136382  0.418115  
4   1.834803           0.278782              0.135590  0.422536  
16  1.816803           0.277504              0.136231  0.412365  
5   1.816212           0.276298              0.135611  0.4145

In [8]:
asset = 'jqdata.000300_XSHG|1d'
# asset = 'jqdata.000905_XSHG'
# asset = 'jqdata.000932_XSHG'

lstparams = []

ema0 = 30
ema1 = 51

buy0 = trdb2py.trading2_pb2.CtrlCondition(
    name='indicatorsp',
    operators=['upcross'],
    strVals=['ema.{}'.format(ema0)],
)

buy1 = trdb2py.trading2_pb2.CtrlCondition(
    name='waittostart',
    vals=[ema0],
)

buy2 = trdb2py.trading2_pb2.CtrlCondition(
    name='indicatorsp',
    operators=['up'],
    strVals=['ema.{}'.format(ema1)],
)

buy3 = trdb2py.trading2_pb2.CtrlCondition(
    name='waittostart',
    vals=[ema1],
)        

sell0 = trdb2py.trading2_pb2.CtrlCondition(
    name='indicatorsp',
    operators=['downcross'],
    strVals=['ema.{}'.format(ema0)],
)

s0 = trdb2py.trading2_pb2.Strategy(
    name="normal",
    asset=trdb2py.str2asset(asset),
)

s0.buy.extend([buy0, buy1, buy2, buy3])
s0.sell.extend([sell0])
s0.paramsBuy.CopyFrom(paramsbuy)
s0.paramsSell.CopyFrom(paramssell) 
s0.paramsInit.CopyFrom(paramsinit)        
lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
    assets=[trdb2py.str2asset(asset)],
    startTs=tsStart,
    endTs=tsEnd,
    strategies=[s0],
    title='ema{}&ema{}'.format(ema0, ema1),
))
 
lstpnlmix = trdb2py.simTradings(trdb2cfg, lstparams, ignoreTotalReturn=2)

trdb2py.showPNLs(lstpnlmix + [pnlBaseline], toImg=isStaticImg, width=width, height=height)

这里策略复杂了一些，考虑了2条均线，可以明显看出，最好的策略相比单均线，有了明显的提升。

In [9]:
lstparams = []

for ema0 in range(2, 61):
    for ema1 in range(ema0, 61):
        for ema2 in range(ema1, 61):
            buy0 = trdb2py.trading2_pb2.CtrlCondition(
                name='indicatorsp',
                operators=['upcross'],
                strVals=['ema.{}'.format(ema0)],
            )

            buy1 = trdb2py.trading2_pb2.CtrlCondition(
                name='waittostart',
                vals=[ema0],
            )

            buy2 = trdb2py.trading2_pb2.CtrlCondition(
                name='indicatorsp',
                operators=['up'],
                strVals=['ema.{}'.format(ema1)],
            )

            buy3 = trdb2py.trading2_pb2.CtrlCondition(
                name='waittostart',
                vals=[ema1],
            )        

            sell0 = trdb2py.trading2_pb2.CtrlCondition(
                name='indicatorsp',
                operators=['downcross'],
                strVals=['ema.{}'.format(ema2)],
            )

            s0 = trdb2py.trading2_pb2.Strategy(
                name="normal",
                asset=trdb2py.str2asset(asset),
            )

            s0.buy.extend([buy0, buy1, buy2, buy3])
            s0.sell.extend([sell0])
            s0.paramsBuy.CopyFrom(paramsbuy)
            s0.paramsSell.CopyFrom(paramssell) 
            s0.paramsInit.CopyFrom(paramsinit)        
            lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
                assets=[trdb2py.str2asset(asset)],
                startTs=tsStart,
                endTs=tsEnd,
                strategies=[s0],
                title='ema{}&ema{}&ema{}'.format(ema0, ema1, ema2),
            ))
 
# lstpnlmix = trdb2py.simTradings(trdb2cfg, lstparams, ignoreTotalReturn=3.2)

# trdb2py.showPNLs(lstpnlmix + [pnlBaseline], toImg=isStaticImg, width=width, height=height)

In [10]:
dfpnl = trdb2py.buildPNLReport(lstpnlmix + [pnlBaseline])

dfpnl1 = dfpnl[dfpnl['totalReturns'] > 3]

# dfpnl1[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)

In [11]:
# asset = 'jqdata.000300_XSHG'
# asset = 'jqdata.000905_XSHG'
asset = 'jqdata.000932_XSHG|1d'

lstparams = []

ema0 = 5
ema1 = 9
ema2 = 29

buy0 = trdb2py.trading2_pb2.CtrlCondition(
    name='indicatorsp',
    operators=['upcross'],
    strVals=['ema.{}'.format(ema0)],
)

buy1 = trdb2py.trading2_pb2.CtrlCondition(
    name='waittostart',
    vals=[ema0],
)

buy2 = trdb2py.trading2_pb2.CtrlCondition(
    name='indicatorsp',
    operators=['up'],
    strVals=['ema.{}'.format(ema1)],
)

buy3 = trdb2py.trading2_pb2.CtrlCondition(
    name='waittostart',
    vals=[ema1],
)        

sell0 = trdb2py.trading2_pb2.CtrlCondition(
    name='indicatorsp',
    operators=['downcross'],
    strVals=['ema.{}'.format(ema2)],
)

s0 = trdb2py.trading2_pb2.Strategy(
    name="normal",
    asset=trdb2py.str2asset(asset),
)

s0.buy.extend([buy0, buy1, buy2, buy3])
s0.sell.extend([sell0])
s0.paramsBuy.CopyFrom(paramsbuy)
s0.paramsSell.CopyFrom(paramssell) 
s0.paramsInit.CopyFrom(paramsinit)        
lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
    assets=[trdb2py.str2asset(asset)],
    startTs=tsStart,
    endTs=tsEnd,
    strategies=[s0],
    title='ema{}&ema{}&ema{}'.format(ema0, ema1, ema2),
))
 
lstpnlmix = trdb2py.simTradings(trdb2cfg, lstparams, ignoreTotalReturn=3)

trdb2py.showPNLs(lstpnlmix + [pnlBaseline], toImg=isStaticImg, width=width, height=height)

我们把策略继续做复杂，就会发现还能有提升，但切换到回测数据以外的数据，会发现其实还不如上次的

这个也很好理解，我们拿一套数据，不断的细分拟合，不断加限制条件，条件越多，肯定越容易得到一个好的盈利曲线

但这种很容易就过拟合，并不一定适用更多的情况

特别对均线来说，如果粒度太小，是很容易过拟合的

对沪深300来说，基本上只要能经过2个牛市，就至少是10倍以上的回报

第一次积累筹码，第二次很容易就能得到一个很大的提升

均线策略不太能跨品种，也就是说沪深300的，不能简单的切到上证500来用

但波动越大，肯定收益越高

In [12]:
lstparams = []

for ema0 in range(2, 61):
    for ema1 in range(2, 61):
        buy0 = trdb2py.trading2_pb2.CtrlCondition(
            name='indicatordp',
            operators=['upcross'],
            strVals=['ema.{}'.format(ema0), 'ema.{}'.format(ema1)],
        )

        buy1 = trdb2py.trading2_pb2.CtrlCondition(
            name='waittostart',
            vals=[ema0],
        )
        
        buy2 = trdb2py.trading2_pb2.CtrlCondition(
            name='waittostart',
            vals=[ema1],
        )        

        sell0 = trdb2py.trading2_pb2.CtrlCondition(
            name='indicatordp',
            operators=['downcross'],
            strVals=['ema.{}'.format(ema0), 'ema.{}'.format(ema1)],
        )

        s0 = trdb2py.trading2_pb2.Strategy(
            name="normal",
            asset=trdb2py.str2asset(asset),
        )

        s0.buy.extend([buy0, buy1, buy2])
        s0.sell.extend([sell0])
        s0.paramsBuy.CopyFrom(paramsbuy)
        s0.paramsSell.CopyFrom(paramssell) 
        s0.paramsInit.CopyFrom(paramsinit)        
        lstparams.append(trdb2py.trading2_pb2.SimTradingParams(
            assets=[trdb2py.str2asset(asset)],
            startTs=tsStart,
            endTs=tsEnd,
            strategies=[s0],
            title='ema{}&ema{}'.format(ema0, ema1),
        ))
 
lstpnlmix = trdb2py.simTradings(trdb2cfg, lstparams, ignoreTotalReturn=3)

# trdb2py.showPNLs(lstpnlmix + [pnlBaseline], toImg=isStaticImg, width=width, height=height)

_MultiThreadedRendezvous: <_MultiThreadedRendezvous of RPC that terminated with:
	status = StatusCode.UNAVAILABLE
	details = "Socket closed"
	debug_error_string = "{"created":"@1609422146.243051500","description":"Error received from peer ipv4:47.244.154.38:5002","file":"src/core/lib/surface/call.cc","file_line":1062,"grpc_message":"Socket closed","grpc_status":14}"
>

In [ ]:
dfpnl = trdb2py.buildPNLReport(lstpnlmix + [pnlBaseline])

dfpnl1 = dfpnl[dfpnl['totalReturns'] > 3]

dfpnl1[['title', 'maxDrawdown', 'maxDrawdownStart', 'maxDrawdownEnd', 'totalReturns', 'sharpe', 'annualizedReturns', 'annualizedVolatility', 'variance']].sort_values(by='totalReturns', ascending=False)